## **Fase 1 - Extract**
*En esta fase inicial, el enfoque está en la extracción de datos brutos directamente desde la plataforma de Airbnb. Utilizando un scraper automatizado, extraemos información esencial sobre las propiedades disponibles, como ubicación, precios, tipo de alojamiento, disponibilidad y reseñas de los usuarios. La extracción es un paso crucial para asegurar que todos los datos relevantes se reúnan y estén listos para su análisis. Nos aseguramos de que los datos se extraigan de forma precisa y consistente, lo cual es fundamental para el éxito de las fases siguientes del proceso. El objetivo de esta fase es consolidar la información extraída en un formato accesible (DataFrame) de manera eficiente y automatizada, para que posteriormente puedan ser limpiados y transformados.* **(necesita edicion - version test)**

In [82]:
# ETL imports
import requests 
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.keys import Keys



# General 
from datetime import datetime
import re
import time
from time import sleep
import pandas as pd
import numpy as np
import json          
import os
import tqdm
from tqdm import tqdm 

In [4]:
opts = Options()
opts.add_argument("user-agent=Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/113.0.0.0 Safari/537.36")

In [5]:
driver = webdriver.Chrome(
    service=Service(ChromeDriverManager().install()),
    options=opts)

# Links to scrapp #

In [ ]:
# Lista de distritos de Barcelona
distritos = [
    "Ciutat Vella",
    "Eixample",
    "Sants-Montjuïc",
    "Les Corts",
    "Sarrià-Sant Gervasi",
    "Gràcia",
    "Horta-Guinardó",
    "Nou Barris",
    "Sant Andreu",
    "Sant Martí"
]

# Creamos una lista para almacenar enlaces de distritos
link_distrito = []

# URL base con el formato de Airbnb
url_base = "https://www.airbnb.es/s/{distrito}--Barcelona--España/homes?tab_id=home_tab&refinement_paths%5B%5D=%2Fhomes&monthly_start_date=2024-11-01&monthly_length=3&monthly_end_date=2025-02-01&price_filter_input_type=0&channel=EXPLORE&query={distrito}%2C%20Barcelona%2C%20España&date_picker_type=calendar&source=structured_search_input_header&search_type=autocomplete_click"

# Iterar sobre cada distrito y generar el enlace
for distrito in distritos:
    # Reemplazar espacios por %20 y caracteres especiales
    distrito_url = distrito.replace(" ", "%20").replace("à", "%C3%A0").replace("ç", "%C3%A7").replace("í", "%C3%AD")
    
    # Formatear el enlace con el nombre del distrito
    enlace = url_base.format(distrito=distrito_url)

    link_distrito.append(enlace)

# Lista vacía para almacenar los links de habitaciones
links_to_scrapp = []

# Accedemos a las paginas de cada distrito
for distrito in tqdm(link_distrito, desc="Accediendo a distritos"):
    
    driver.get(distrito)

    # Pausa
    sleep(3)

    # Bucle para la paginación y extración
    while len(links_to_scrapp) < 2700:  # Limitar a 500 enlaces
        try:
            sleep(2)
            # Obtener el código fuente de la página actual
            page_source = driver.page_source
            soup = BeautifulSoup(page_source, 'html.parser')

            # Extraer todos los enlaces de habitaciones en la página actual
            link_habitacion = driver.find_elements(By.CSS_SELECTOR, 'a[href*="/rooms/"]')

            # Lista de urls target
            links_target = []

            # Recorrer todos los enlaces y filtrar los que contienen '/rooms'
            for _ in link_habitacion:
                link = _.get_attribute('href')
                if link and '/rooms/' in link:
                    links_target.append(link)

            # Eliminar duplicados en la lista de enlaces
            links_filtered = set(links_target)
            print(f"Número de links filtrados en la página: {len(links_filtered)}")

            # Añadimos los links en la lista de scrappeo
            for url in links_filtered:
                if len(links_to_scrapp) < 2700:  # Limitar a 500 enlaces
                    links_to_scrapp.append(url)
                    print(f'Agregando URL: {url}')
                else:
                    break

            print(f"Total de links extraídos hasta ahora: {len(links_to_scrapp)}")

            if len(links_to_scrapp) >= 2700:  
                print('Total de enlaces alcanzado. Deteniendo la extracción......')
                break

            # Pausa antes de hacer click en la próxima página
            sleep(2)

            # Buscar y hacer click en el botón "Siguiente"
            next_button = driver.find_element(By.CSS_SELECTOR, 'a[aria-label="Siguiente"]')
            next_button.click()
            print('Siguiente página...')

        except Exception as e:
            print('No se pudo cargar la siguiente página o no hay más páginas.')
            print(e)
            break

# Imprimir a lista final de enlaces
print("Extracción completa. Total de links:", len(links_to_scrapp))

Accediendo a distritos:   0%|          | 0/10 [00:00<?, ?it/s]

Número de links filtrados en la página: 18
Agregando URL: https://www.airbnb.es/rooms/1123156827645522473?adults=1&category_tag=Tag%3A8678&children=0&enable_m3_private_room=true&infants=0&pets=0&photo_id=1894631759&search_mode=regular_search&check_in=2024-11-05&check_out=2024-11-10&source_impression_id=p3_1730837189_P3OE3lmWPuzFKyll&previous_page_section_name=1000&federated_search_id=a70f0684-6bfc-430c-b5d8-88dac71f85c6
Agregando URL: https://www.airbnb.es/rooms/1270266469340006214?adults=1&category_tag=Tag%3A8678&children=0&enable_m3_private_room=true&infants=0&pets=0&photo_id=2015148890&search_mode=regular_search&check_in=2024-11-25&check_out=2024-11-30&source_impression_id=p3_1730837189_P3mdntJiJLuRuGMB&previous_page_section_name=1000&federated_search_id=a70f0684-6bfc-430c-b5d8-88dac71f85c6
Agregando URL: https://www.airbnb.es/rooms/1176611230178132461?adults=1&children=0&enable_m3_private_room=true&infants=0&pets=0&search_mode=regular_search&check_in=2024-11-10&check_out=2024-11-15

Accediendo a distritos:  10%|█         | 1/10 [01:15<11:18, 75.39s/it]

No se pudo cargar la siguiente página o no hay más páginas.
Message: no such element: Unable to locate element: {"method":"css selector","selector":"a[aria-label="Siguiente"]"}
  (Session info: chrome=130.0.6723.92); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#no-such-element-exception
Stacktrace:
	GetHandleVerifier [0x003A3913+24035]
	(No symbol) [0x0032BCA4]
	(No symbol) [0x0020C2D3]
	(No symbol) [0x0024DC86]
	(No symbol) [0x0024DECB]
	(No symbol) [0x0028B9D2]
	(No symbol) [0x0026FED4]
	(No symbol) [0x0028953F]
	(No symbol) [0x0026FC26]
	(No symbol) [0x0024218C]
	(No symbol) [0x0024310D]
	GetHandleVerifier [0x00649743+2800659]
	GetHandleVerifier [0x006A42FE+3172302]
	GetHandleVerifier [0x0069CF12+3142626]
	GetHandleVerifier [0x00446CC0+692624]
	(No symbol) [0x00334CBD]
	(No symbol) [0x003319C8]
	(No symbol) [0x00331B60]
	(No symbol) [0x00324010]
	BaseThreadInitThunk [0x74FE7BA9+25]
	RtlInitializeExceptionChain

Accediendo a distritos:  20%|██        | 2/10 [02:18<09:03, 67.92s/it]

Número de links filtrados en la página: 18
Agregando URL: https://www.airbnb.es/rooms/1265836369331663483?adults=1&children=0&enable_m3_private_room=true&infants=0&pets=0&search_mode=regular_search&check_in=2024-11-09&check_out=2024-11-14&source_impression_id=p3_1730837323_P321AR3XyjiCLOZV&previous_page_section_name=1000&federated_search_id=7d60375a-b4d3-443c-aefc-5a3086d900ea
Agregando URL: https://www.airbnb.es/rooms/644609319092681892?adults=1&children=0&enable_m3_private_room=true&infants=0&pets=0&search_mode=regular_search&check_in=2024-11-24&check_out=2024-11-29&source_impression_id=p3_1730837323_P3ZzRyP63lSOyH85&previous_page_section_name=1000&federated_search_id=7d60375a-b4d3-443c-aefc-5a3086d900ea
Agregando URL: https://www.airbnb.es/rooms/39753264?adults=1&children=0&enable_m3_private_room=true&infants=0&pets=0&search_mode=regular_search&check_in=2024-11-10&check_out=2024-11-15&source_impression_id=p3_1730837323_P3lzQh_PRHmmZo06&previous_page_section_name=1000&federated_searc

Accediendo a distritos: 100%|██████████| 10/10 [02:57<00:00, 17.72s/it]

Extracción completa. Total de links: 500


# Informacion General #

In [ ]:
now = datetime.now()

# Función para extraer el texto de un elemento dado
def extract_text(soup, tag, class_name, index=0, default=np.nan):
    try:
        elements = soup.find_all(tag, class_=class_name)
        return elements[index].text.strip() if elements else default  # Retorna el texto del elemento especificado
    except (AttributeError, IndexError):
        return default

# Diccionario para los campos a extraer, organizados en el orden deseado
fields = {
    "Titles": ("span", "l1h825yc", 1),  # Título del alojamiento
    "Host_name": ("div", "t1pxe1a4", 0),  # Nombre del anfitrión
    "Property_types": ("h2", "hpipapi", 0),  # Tipo de propiedad
    "Prices_per_night": ("span", "_11jcbg2", 0),  # Precio por noche
    "Check_ins": ("div", "i1303y2k", 0),  # Check-in
    "Check_outs": ("div", "i1303y2k", 1),  # Check-out
    "Location": ("div", "_152qbzi", 0),  # Ubicación
}

# Limitar a 500 enlaces para la muestra
sample_links = links_to_scrapp

# Lista para almacenar los datos extraídos
data_list = []

# Iterar sobre cada enlace en la muestra
for link in tqdm(sample_links, desc="Extrayendo datos"):
    if 'adults' not in link:
        # Verificar si ya hay parámetros en la URL
        if '?' in link:
            link += '&adults=1'  # Agregar & si ya hay otros parámetros
        else:
            link += '?adults=1'  # Agregar ? si no hay parámetros

    print(f"Accediendo a: {link}")        

    driver.get(link)  # Acceder a la página
    sleep(5)  # Espera para cargar la página

    # Obtener el objeto BeautifulSoup
    page_source = driver.page_source
    soup = BeautifulSoup(page_source, 'html.parser')


    try:
        # Boton de traduccion

        button_trad = WebDriverWait(driver, 3).until(
            EC.element_to_be_clickable((By.XPATH, "//button[@aria-label='Cerrar']"))
        )
        button_trad.click()
        print("Botón de traducción clicado con éxito.")

    except (NoSuchElementException, TimeoutException):
        print("No se encontró el botón de traducción.")
    

        # Capturar el contenido de la página -----------> Provisional
    page_source = driver.page_source
    soup = BeautifulSoup(page_source, 'html.parser')

    data = {
    'urls': link,
    'timestamp': now.strftime('%Y-%m-%d %H:%M:%S'),  # Añadir la fecha y hora formateada
    'record_id': link.split('/')[-1].split('?')[0]  # Usar el ID de la URL como record_id
    }

    # Extraer usando el diccionario y la función de extracción
    data.update({field: extract_text(soup, *details) for field, details in fields.items()})

    # Obtener las reseñas y calificaciones usando XPATH
    ratings_xpaths = [
        "/html/body/div[5]/div/div/div[1]/div/div[2]/div/div/div/div[1]/main/div/div[1]/div[3]/div/div[1]/div/div[1]/div/div/div/section/div[3]/div[2]",
        "/html/body/div[5]/div/div/div[1]/div/div[2]/div/div/div/div[1]/main/div/div[1]/div[3]/div/div[1]/div/div[2]/div/div/div/a/div/div[6]/div[1]",
        "/html/body/div[5]/div/div/div[1]/div/div[2]/div/div/div/div[1]/main/div/div[1]/div[3]/div/div[1]/div/div[1]/div/div/div/section/div[3]/div[2]",
    ]

    reviews_xpaths = [
        "/html/body/div[5]/div/div/div[1]/div/div[2]/div/div/div/div[1]/main/div/div[1]/div[3]/div/div[1]/div/div[1]/div/div/div/section/div[3]/a",
        "/html/body/div[5]/div/div/div[1]/div/div[2]/div/div/div/div[1]/main/div/div[1]/div[3]/div/div[1]/div/div[2]/div/div/div/a/div/div[10]/div[1]",
        "/html/body/div[5]/div/div/div[1]/div/div[2]/div/div/div/div[1]/main/div/div[1]/div[3]/div/div[1]/div/div[1]/div/div/div/section/div[3]/a",
    ]

    rating = num_reviews = np.nan  # Inicializa como NaN

    # Intentar obtener las calificaciones
    for xpath in ratings_xpaths:
        try:
            rating = driver.find_element(By.XPATH, xpath).text
            break  # Salir del bucle si se encuentra la calificación
        except:
            continue  # Continuar intentando con el siguiente XPATH

    # Intentar obtener el número de reseñas
    for xpath in reviews_xpaths:
        try:
            num_reviews_text = driver.find_element(By.XPATH, xpath).text
            if 'evaluaciones' in num_reviews_text:
                num_reviews = num_reviews_text.split()[0]  # Captura el número de evaluaciones
                break  # Salir del bucle si se encuentra el número de evaluaciones
        except:
            continue  # Continuar intentando con el siguiente XPATH

    # Añadir calificaciones y número de reseñas al diccionario de datos
    data['Ratings'] = rating
    data['Num_reviews'] = num_reviews
    
    # Extraccion de cleaning fee
    try:
        # Buscar el elemento de gastos de limpieza
        cleaning_fee_loc = driver.find_element(By.CSS_SELECTOR, "div[data-plugin-in-point-id='BOOK_IT_SIDEBAR'] div._m495dq")

        # Inicializar variables de comisión y limpieza
        cleaning_fee = 0  
        com_fee = 0
        
        # Buscar el dato de la tarifa con expresión regular
        gastos_limpieza = re.search(r"Gastos de limpieza.*?(\d+ €)", cleaning_fee_loc.text, re.DOTALL)
        comision_gestion = re.search(r"Comisión de servicio de Airbnb.*?(\d+ €)", cleaning_fee_loc.text, re.DOTALL)
        
        if gastos_limpieza:
            cleaning_fee = gastos_limpieza.group(1)

        if comision_gestion :
            com_fee = comision_gestion.group(1)


    except Exception as e:
        
        print(f"No se pudo encontrar el elemento de gastos de limpieza o comisión de servicio: {e}")
        cleaning_fee = "Error al encontrar el elemento de gastos de limpieza"
        com_fee = "Error al encontrar el elemento de comisión de servicio"

    # Añadir el cleaning_fee al diccionario de datos
    data['Cleaning_fee'] = cleaning_fee
    data['Com_fee'] = com_fee
    

    # Extracción de detalles (camas, baños, etc.) usando el selector CSS
    details = driver.find_elements(By.CSS_SELECTOR, "div.o1kjrihn ol.lgx66tx")
    detalles = [_.text for _ in details]

    # Procesar cada detalle y categorizar
    detalles_limpio = {}
    for i in detalles:
        for fragment in i.split(" · "):
            # Detecta y asigna cada categoría por palabras clave en cada fragmento
            if "viajero" in fragment:
                detalles_limpio['Viajeros'] = fragment
            elif "dormitorio" in fragment:
                detalles_limpio['Dormitorios'] = fragment
            elif "cama" in fragment:
                detalles_limpio['Camas'] = fragment
            elif "baño" in fragment or "Baño" in fragment:
                detalles_limpio['Baños'] = fragment
            else:
                detalles_limpio['Otros'] = fragment

    # Agregar detalles categorizados al diccionario de datos sin afectar los campos existentes
    data.update(detalles_limpio)

    # Agregar el número máximo de huéspedes
    n_guests = driver.find_elements(By.CSS_SELECTOR, "div[data-plugin-in-point-id='POLICIES_DEFAULT'] div.i1303y2k span")
    guests_count = np.nan  # Valor predeterminado en caso de no encontrar
    for guest in n_guests:
        if 'huésped' in guest.text or 'huéspedes' in guest.text:
            guests_count = guest.text.split()[1]  # Extraer solo el número de huéspedes
            break  # Salir del bucle si se encuentra el número de huéspedes

    # Añadir el número máximo de huéspedes al diccionario de datos
    data['Maximum_guests'] = guests_count

    # Añadir los datos extraídos a la lista
    data_list.append(data)

# Crear el DataFrame final con los datos extraídos
df = pd.DataFrame(data_list)

Extrayendo datos:   0%|          | 0/500 [00:00<?, ?it/s]

Accediendo a: https://www.airbnb.es/rooms/1123156827645522473?adults=1&category_tag=Tag%3A8678&children=0&enable_m3_private_room=true&infants=0&pets=0&photo_id=1894631759&search_mode=regular_search&check_in=2024-11-05&check_out=2024-11-10&source_impression_id=p3_1730837189_P3OE3lmWPuzFKyll&previous_page_section_name=1000&federated_search_id=a70f0684-6bfc-430c-b5d8-88dac71f85c6
Botón de traducción clicado con éxito.


Extrayendo datos:   0%|          | 1/500 [00:05<47:04,  5.66s/it]

Accediendo a: https://www.airbnb.es/rooms/1270266469340006214?adults=1&category_tag=Tag%3A8678&children=0&enable_m3_private_room=true&infants=0&pets=0&photo_id=2015148890&search_mode=regular_search&check_in=2024-11-25&check_out=2024-11-30&source_impression_id=p3_1730837189_P3mdntJiJLuRuGMB&previous_page_section_name=1000&federated_search_id=a70f0684-6bfc-430c-b5d8-88dac71f85c6


Extrayendo datos:   0%|          | 2/500 [00:14<1:01:12,  7.37s/it]

...

No se encontró el botón de traducción.
Accediendo a: https://www.airbnb.es/rooms/572279772505856997?adults=1&children=0&enable_m3_private_room=true&infants=0&pets=0&search_mode=regular_search&check_in=2024-11-05&check_out=2024-11-10&source_impression_id=p3_1730837323_P3d538xXf5OOd1mV&previous_page_section_name=1000&federated_search_id=7d60375a-b4d3-443c-aefc-5a3086d900ea


Extrayendo datos: 100%|█████████▉| 499/500 [1:10:44<00:08,  8.50s/it]

No se encontró el botón de traducción.
Accediendo a: https://www.airbnb.es/rooms/1249192751408741394?adults=1&category_tag=Tag%3A8678&children=0&enable_m3_private_room=true&infants=0&pets=0&photo_id=1996677985&search_mode=regular_search&check_in=2024-11-12&check_out=2024-11-17&source_impression_id=p3_1730837323_P3w2ZDNZ-l5NGgJe&previous_page_section_name=1000&federated_search_id=7d60375a-b4d3-443c-aefc-5a3086d900ea


Extrayendo datos: 100%|██████████| 500/500 [1:10:53<00:00,  8.51s/it]

No se encontró el botón de traducción.


In [16]:
df

urls            timestamp  \
0    https://www.airbnb.es/rooms/112315682764552247...  2024-11-05 21:31:53   
1    https://www.airbnb.es/rooms/127026646934000621...  2024-11-05 21:31:53   
2    https://www.airbnb.es/rooms/117661123017813246...  2024-11-05 21:31:53   
3    https://www.airbnb.es/rooms/114769274640194057...  2024-11-05 21:31:53   
4    https://www.airbnb.es/rooms/936143488605005872...  2024-11-05 21:31:53   
..                                                 ...                  ...   
495  https://www.airbnb.es/rooms/52047123?adults=1&...  2024-11-05 21:31:53   
496  https://www.airbnb.es/rooms/862122500288513146...  2024-11-05 21:31:53   
497  https://www.airbnb.es/rooms/121658361041847639...  2024-11-05 21:31:53   
498  https://www.airbnb.es/rooms/572279772505856997...  2024-11-05 21:31:53   
499  https://www.airbnb.es/rooms/124919275140874139...  2024-11-05 21:31:53   

               record_id                                             Titles  \
0    1123156827645522473  Esta acogedora habitación  cuenta con una cómo...   
1    1270266469340006214  Cancelación gratuita antes del 24 nov. Si canc...   
2    1176611230178132461  Desconecta de la rutina en este alojamiento ún...   
3    1147692746401940575  Acogedora habitación individual en el bullicio...   
4     936143488605005872  Este alojamiento tiene una ubicación estratégi...   
..                   ...                                                ...   
495             52047123  Acogedora habitación doble. Esta habitación lu...   
496   862122500288513146  Nuestras habitaciones dobles estándar son pequ...   
497  1216583610418476390  Habitación amplia, confortable  con luz natura...   
498   572279772505856997  > DORMITORIO FEMENINO <Precioso albergue juven...   
499  1249192751408741394  Disfruta de la sencillez de este alojamiento t...   

                      Host_name  \
0            Quédate con Manuel   
1               Anfitrión: Joar   
2            Anfitrión: Badajoz   
3    Anfitrión: Victoria Isabel   
4      Quédate con Cat Y Jhosep   
..                          ...   
495           Anfitrión: Hostal   
496          Anfitrión: Lorenzo   
497             Anfitrión: Sara   
498           Anfitrión: Eduard   
499           Quédate con Maria   

                                        Property_types Prices_per_night  \
0                      Habitación en Barcelona, España             45 €   
1                      Habitación en Barcelona, España             46 €   
2    Alojamiento entero: apartamento en Barcelona, ...            100 €   
3                      Habitación en Barcelona, España             44 €   
4                      Habitación en Barcelona, España             33 €   
..                                                 ...              ...   
495  Habitación privada en: hostal en Barcelona, Es...             66 €   
496  Habitación privada en: hostal en Barcelona, Es...            100 €   
497                    Habitación en Barcelona, España             51 €   
498                    Habitación en Barcelona, España             34 €   
499                    Habitación en Barcelona, España             83 €   

                                Check_ins                 Check_outs  \
0           Llegada a partir de las 15:00  Salida antes de las 12:00   
1           Llegada a partir de las 10:00  Salida antes de las 12:00   
2           Llegada a partir de las 15:00  Salida antes de las 11:00   
3    Horario de llegada: de 15:00 a 21:00   Salida antes de las 9:00   
4    Horario de llegada: de 15:00 a 22:00  Salida antes de las 11:00   
..                                    ...                        ...   
495   Horario de llegada: de 14:00 a 2:00  Salida antes de las 11:00   
496         Llegada a partir de las 15:00  Salida antes de las 12:00   
497         Llegada a partir de las 14:00  Salida antes de las 11:00   
498         Llegada a partir de las 14:00  Salida antes de las 10:00   
499  Horario de llegada: de 15:00 a 21

In [18]:
df.shape

(500, 20)

In [20]:
df.to_csv('df_sample_V3.csv', index = False)

# Servicios airbnb #

In [22]:
# Creamos un diccionario para almacenar los servicios por categoría
datos_airbnb = dict()

for link in tqdm(sample_links, desc="Extrayendo datos"):

    servicios_por_categoria = dict()

    # Accedemos a cada link
    print(f"Accediendo a: {link}")  # Imprimir el enlace que se está visitando
    driver.get(link)
    sleep(3)

    try:
        # Boton de traduccion
    
        button_trad = WebDriverWait(driver, 3).until(
            EC.element_to_be_clickable((By.XPATH, "//button[@aria-label='Cerrar']"))
        )
        button_trad.click()
        print("Botón de traducción clicado con éxito.")

    except (NoSuchElementException, TimeoutException):
        print("No se encontró el botón de traducción.")

    # Buscar y hacer clic en el botón de "Siguiente"
   
    try:
        button = driver.find_element(By.XPATH, "//button[contains(text(), 'Mostrar los')]")
        button.click()
           # Capturar el contenido de la página
        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')


        sleep(5)
        
        # Capturar el contenido de la página
        page_source = driver.page_source
        soup = BeautifulSoup(page_source, 'html.parser')
        
    
        # Encuentra todas las secciones de servicios
        secciones = soup.select('section div._11jhslp h2.hpipapi')
        print(len(secciones))
    
        # Iteramos sobre cada sección
        for seccion in secciones:
            # Título de la categoría (por ejemplo, "Baño", "Entretenimiento", etc.)
            categoria = seccion.text.strip()
    
            servicios_por_categoria[categoria] = list()
            
            # Encuentra la lista de servicios que pertenece a esa categoría
            servicios = seccion.find_next('ul').find_all('li')
        
            # Añadimos los servicios al diccionario bajo la categoría correspondiente
            for servicio in servicios:
                servicio_limpio = servicio.text.strip()
                servicios_por_categoria[categoria].append(servicio_limpio)
    
        datos_airbnb[link] = servicios_por_categoria
        # Ahora imprimimos los servicios por categoría
        for categoria, servicios in servicios_por_categoria.items():
            print(f"Categoría: {categoria}")
            for servicio in servicios:
                print(f"  - {servicio}")
    except NoSuchElementException:
        print("El botón no está disponible en esta página.")



Accediendo a: https://www.airbnb.es/rooms/1123156827645522473?adults=1&category_tag=Tag%3A8678&children=0&enable_m3_private_room=true&infants=0&pets=0&photo_id=1894631759&search_mode=regular_search&check_in=2024-11-05&check_out=2024-11-10&source_impression_id=p3_1730837189_P3OE3lmWPuzFKyll&previous_page_section_name=1000&federated_search_id=a70f0684-6bfc-430c-b5d8-88dac71f85c6
11
Categoría: Baño
  - Secador de pelo
  - Gel de ducha
  - Agua caliente
  - Gel de ducha
Categoría: Dormitorio y lavandería
  - Lavadora
  - Perchas
  - Ropa de cama
  - Persianas o cortinas opacas
  - Plancha
  - Tendedero para ropa
  - Espacio para guardar la ropa
Categoría: Entretenimiento
  - TV
Categoría: Calefacción y refrigeración
  - Ventiladores portátiles
Categoría: Privacidad y seguridad
  - Cerradura en la puerta del dormitorio
Categoría: Internet y oficina
  - Wifi
Categoría: Cocina y comedor
  - CocinaCocina disponible para el uso de los huéspedes
  - Frigorífico
  - Microondas
  - Utensilios bási

In [49]:
len(datos_airbnb)

500

In [51]:
datos_estructurados = list()

# Accedemos a cada url de los diccionarios
for url in datos_airbnb:
    for k, v in datos_airbnb[url].items(): # Hacemos un key-value de cada subdiccionario en cada url
        for elemento in v: # para cada value, iteramos todos los elementos de la lista
            datos_estructurados.append([k, elemento, url])

df_servicios = pd.DataFrame(datos_estructurados, columns = ["Category", "Service", "url"])

In [105]:
df_servicios

Category  \
0                         Baño   
1                         Baño   
2                         Baño   
3                         Baño   
4      Dormitorio y lavandería   
...                        ...   
16029             No incluidos   
16030             No incluidos   
16031             No incluidos   
16032             No incluidos   
16033             No incluidos   

                                                 Service  \
0                                        Secador de pelo   
1                                           Gel de ducha   
2                                          Agua caliente   
3                                           Gel de ducha   
4                                               Lavadora   
...                                                  ...   
16029  No disponible: Aire acondicionadoAire acondici...   
16030  No disponible: Servicios básicosServicios básicos   
16031  No disponible: Detector de humoDetector de hum...   
16032              No disponible: CalefacciónCalefacción   
16033          No disponible: Agua calienteAgua caliente   

                                                     url  
0      https://www.airbnb.es/rooms/112315682764552247...  
1      https://www.airbnb.es/rooms/112315682764552247...  
2      https://www.airbnb.es/rooms/112315682764552247...  
3      https://www.airbnb.es/rooms/112315682764552247...  
4      https://www.airbnb.es/rooms/112315682764552247...  
...                                                  ...  
16029  https://www.airbnb.es/rooms/124919275140874139...  
16030  https://www.airbnb.es/rooms/124919275140874139...  
16031  https://www.airbnb.es/rooms/124919275140874139...  
16032  https://www.airbnb.es/rooms/124919275140874139...  
16033  https://www.airbnb.es/rooms/124919275140874139...  

[16034 rows x 3 columns]

In [53]:
df_servicios.shape

(16034, 3)

In [62]:
df_servicios.to_csv('df_servicios_V3.csv', index = False)

# Star rating - Comentarios #

In [ ]:
# Lista para almacenar el zip
lista_comentarios = list()

for link in tqdm(sample_links, desc="Extrayendo datos"):
    driver.get(link)
    print(f'accediendo al link: {link}')
    sleep(2)

    try:
        # Boton de traduccion
    
        button_trad = WebDriverWait(driver, 3).until(
            EC.element_to_be_clickable((By.XPATH, "//button[@aria-label='Cerrar']"))
        )
        button_trad.click()
        print("Botón de traducción clicado con éxito.")

    except (NoSuchElementException, TimeoutException):
        print("No se encontró el botón de traducción.")

    button = driver.find_elements(By.CSS_SELECTOR, 'button[data-testid="pdp-show-all-reviews-button"]')

    if button:
        
        try:
            # Click en el boton de comentarios
            button[0].click()
            sleep(2)
            
            # Nos situamos en el scroller de comentarios
            element_inside_popup = driver.find_element(by = By.XPATH, value = "/html/body/div[9]/div/div/section/div/div/div[2]/div/div[3]")
            
            # Establecemos un contador de comentarios
            total_comentarios = 0
            
            # Bucle para mantener scroll
            while True:
            
                # Scroll hasta abajo del bar
                element_inside_popup.send_keys(Keys.END)
                
                sleep(2)
            
                # Capturamos contenido nuevo con bs4 
                soup_comentarios = BeautifulSoup(driver.page_source, "html.parser")
            
                # Almacenamos el numero de comentarios
                nuevo_total_comentarios = len(soup_comentarios.find_all("div", class_ = "r1are2x1 atm_gq_1vi7ecw dir dir-ltr"))
                print(f'nuevo total comentarios: {nuevo_total_comentarios}')
            
                if total_comentarios == nuevo_total_comentarios:
                    print('final comentarios')
                    break
                else:
                    total_comentarios = nuevo_total_comentarios
                    
            
                sleep(1)
    
            star_rat = driver.find_elements(By.CSS_SELECTOR,  "div[data-testid='pdp-reviews-modal-scrollable-panel'] div.c5dn5hn.atm_9s_1txwivl.atm_cx_t94yts.dir.dir-ltr span.a8jt5op.atm_3f_idpfg4.atm_7h_hxbz6r.atm_7i_ysn8ba.atm_e2_t94yts.atm_ks_zryt35.atm_l8_idpfg4.atm_mk_stnw88.atm_vv_1q9ccgz.atm_vy_t94yts.dir.dir-ltr" )
    
        # Encuentra todos los spans que contienen comentarios
        # Asegúrate de que el selector sea el adecuado para tu caso
            comentarios = driver.find_elements(By.CSS_SELECTOR, "div[data-testid='pdp-reviews-modal-scrollable-panel'] div.r1bctolv span.l1h825yc.atm_kd_19r6f69_24z95b.atm_kd_19r6f69_1xbvphn_1oszvuo.dir.dir-ltr" )
    
    
            for a, b in zip(star_rat, comentarios):
                lista_comentarios.append([a.text, b.text, driver.current_url, datetime.now()])
                print('añadiendo elementos')

        except NoSuchElementException:
            print(f'el url {link} no tiene reviews')
        except Exception as e:
            print(f'error en url {link} : {e}')

    else:
        star_rat_2 = driver.find_elements(By.CSS_SELECTOR,  "div.c5dn5hn span.a8jt5op" )
        comentarios_2 = driver.find_elements(By.CSS_SELECTOR,  "div.r1bctolv span.l1h825yc" )
        print('añadiendo elementos sin boton')

        for a, b in zip(star_rat_2, comentarios_2):
            lista_comentarios.append([a.text, b.text, driver.current_url, datetime.now()])

accediendo al link: https://www.airbnb.es/rooms/1123156827645522473?adults=1&category_tag=Tag%3A8678&children=0&enable_m3_private_room=true&infants=0&pets=0&photo_id=1894631759&search_mode=regular_search&check_in=2024-11-05&check_out=2024-11-10&source_impression_id=p3_1730837189_P3OE3lmWPuzFKyll&previous_page_section_name=1000&federated_search_id=a70f0684-6bfc-430c-b5d8-88dac71f85c6
añadiendo elementos sin boton
accediendo al link: https://www.airbnb.es/rooms/1270266469340006214?adults=1&category_tag=Tag%3A8678&children=0&enable_m3_private_room=true&infants=0&pets=0&photo_id=2015148890&search_mode=regular_search&check_in=2024-11-25&check_out=2024-11-30&source_impression_id=p3_1730837189_P3mdntJiJLuRuGMB&previous_page_section_name=1000&federated_search_id=a70f0684-6bfc-430c-b5d8-88dac71f85c6
añadiendo elementos sin boton
accediendo al link: https://www.airbnb.es/rooms/1176611230178132461?adults=1&children=0&enable_m3_private_room=true&infants=0&pets=0&search_mode=regular_search&check_in

In [90]:
df_coments = pd.DataFrame(np.array(lista_comentarios), columns = ['Rating', 'Comentario', 'Url', 'Timestamp'])

In [92]:
df_coments.shape

(93372, 4)

In [94]:
df_coments

Rating  \
0      Valoración: 5 estrellas   
1      Valoración: 3 estrellas   
2      Valoración: 4 estrellas   
3      Valoración: 4 estrellas   
4      Valoración: 5 estrellas   
...                        ...   
93367  Valoración: 5 estrellas   
93368  Valoración: 5 estrellas   
93369  Valoración: 5 estrellas   
93370  Valoración: 5 estrellas   
93371  Valoración: 5 estrellas   

                                              Comentario  \
0      Claudia fue extremadamente servicial y amable,...   
1      habitación actual muy pequeña hecha con un cab...   
2      Buena relación calidad-precio, pero...\nAunque...   
3      Ideal para un viaje corto por la ciudad. El do...   
4                                 Todo muy bien. Gracias   
...                                                  ...   
93367         Ubicación perfecta y personal super amable   
93368  Todo era perfecto allí. Recomiendo absolutamen...   
93369  Tuve una experiencia increíble en el hostal de...   
93370  Pasé un tiempo estupendo en el departamento de...   
93371  Nos lo pasamos muy bien en casa de María que n...   

                                                     Url  \
0      https://www.airbnb.es/rooms/936143488605005872...   
1      https://www.airbnb.es/rooms/936143488605005872...   
2      https://www.airbnb.es/rooms/936143488605005872...   
3      https://www.airbnb.es/rooms/936143488605005872...   
4      https://www.airbnb.es/rooms/936143488605005872...   
...                                                  ...   
93367  https://www.airbnb.es/rooms/572279772505856997...   
93368  https://www.airbnb.es/rooms/572279772505856997...   
93369  https://www.airbnb.es/rooms/572279772505856997...   
93370  https://www.airbnb.es/rooms/124919275140874139...   
93371  https://www.airbnb.es/rooms/124919275140874139...   

                       Timestamp  
0     2024-11-06 04:33:22.745926  
1     2024-11-06 04:33:22.754516  
2     2024-11-06 04:33:22.763587  
3     2024-11-06 04:33:22.772815  
4     2024-11-06 04:33:22.780329  
...                          ...  
93367 2024-11-06 18:13:12.718121  
93368 2024-11-06 18:13:12.727124  
93369 2024-11-06 18:13:12.736126  
93370 2024-11-06 18:13:16.019508  
93371 2024-11-06 18:13:16.031511  

[93372 rows x 4 columns]

In [96]:
df_coments.to_csv('df_comentsV3.csv', index = False)